# Setup

In [ ]:
%pip install transformers
%pip install bitsandbytes
%pip install accelerate
%pip install torch
%pip install huggingface_hub
# %pip install --upgrade --quiet elasticsearch langchain-elasticsearch
# %pip install --quiet --upgrade langchain langchain-community langchain-chroma
%pip install datasets
%pip install nltk
%pip install sentence_transformers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.0/76.0 MB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 55.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 32.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 44.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 14.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 51.5 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstallin

In [ ]:
%pip install rouge-score

  Preparing metadata (setup.py) ... done
  Created wheel for rouge-score: filename=rouge_score-0.1.2-py3-none-any.whl size=24935 sha256=889ade1fd5072c07e4d098b64544141e71da0a1db3f82a6d9feaf2aabcc0388d
  Stored in directory: /root/.cache/pip/wheels/1e/19/43/8a442dc83660ca25e163e1bd1f89919284ab0d0c1475475148
Successfully built rouge-score


In [ ]:
import getpass
import os
import time
import math
import ast
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import re
import json
import csv
from typing import Any, Dict, Iterable
from google.colab import drive
from google.colab import userdata
from huggingface_hub import login
# from datasets import load_dataset
import torch
import torch.nn.functional as F
from transformers import AutoTokenizer, AutoModelForCausalLM
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from sentence_transformers import SentenceTransformer

os.environ["HF_TOKEN"] = userdata.get("HF_TOKEN")
login(os.environ["HF_TOKEN"])

Note: Environment variable`HF_TOKEN` is set and is the current active token independently from the token you've just configured.


# Experiment 1

Datasets: SQuAD 2.0, GSM8K, TruthfulQA

1. Sequence Likelihood
2. Perplexity (Length-normalised sequence likelihood) Predictive Entropy
3. P(True) (prompt provided below)
4. Lexical Similarity
5. Semantic entropy
6. Eccentricity
7. Verbalised Confidence

In [ ]:
model_name = "meta-llama/Llama-3.1-8B-Instruct"
model = AutoModelForCausalLM.from_pretrained(model_name, torch_dtype=torch.bfloat16, device_map="cuda")
tokenizer = AutoTokenizer.from_pretrained(model_name)

config.json:   0%|          | 0.00/855 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/23.9k [00:00<?, ?B/s]

Fetching 4 files:   0%|          | 0/4 [00:00<?, ?it/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

model-00002-of-00004.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

...

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/184 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/55.4k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/9.09M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

## Helper functions (dataset agnostic)


In [ ]:
def generate(model, tokenizer, messages, user_question):
    """
    :param model: model
    :param tokenizer: tokenizer
    :param messages: conversation
    :param user_question: user_question
    :return: outputs, input_ids, messages with user_question
    """
    messages.append({"role": "user", "content": user_question})
    input_ids = tokenizer.apply_chat_template(
        messages,
        add_generation_prompt=True,
        return_tensors="pt"
    )
    input_ids = input_ids.to(model.device)

    terminators = [
        tokenizer.eos_token_id,
        tokenizer.convert_tokens_to_ids("<|eot_id|>")
    ]

    start_time = time.time()
    print("--- generate begins ---")

    outputs = model.generate(
        input_ids,
        max_new_tokens=256,
        eos_token_id=terminators,
        do_sample=True,
        temperature=0.6,
        top_p=0.9,
        output_scores=True,
        output_logits=True,
        output_attentions=True,
        return_dict_in_generate=True
    )
    print("--- generate ends, time taken: %s seconds ---" % (time.time() - start_time))
    return outputs, input_ids, messages

# def compute_predictive_entropy(scores):
#     """
#     Compute predictive entropy at each generation step.

#     Args:
#         scores (list[Tensor]): List of logits tensors for each generation step.
#             Each tensor is of shape (num_return_sequences, vocab_size).

#     Returns:
#         list[float]: Predictive entropy computed for each generation step.
#     """
#     entropies = []
#     for step_logits in scores:
#         # Convert logits to probabilities for each sample at this time step.
#         probs = F.softmax(step_logits, dim=-1)  # shape: (num_return_sequences, vocab_size)
#         # Average the distributions over the samples.
#         avg_probs = probs.mean(dim=0)  # shape: (vocab_size)
#         # Compute entropy: - sum(avg_probs * log(avg_probs))
#         entropy = -(avg_probs * torch.log(avg_probs + 1e-12)).sum().item()
#         entropies.append(entropy)
#     return entropies

def compute_sequence_likelihood(input_ids, outputs):
    sequence_likelihood = 0

    for i, logits in enumerate(outputs['logits']):
        # Apply softmax over the last dimension (vocab size) to get probabilities
        probabilities = F.softmax(logits, dim=-1)

        # Get the index of the generated token for this step
        generated_token_id = outputs['sequences'][0][input_ids.shape[-1] + i].item()

        # Get the probability of the generated token
        generated_token_prob = probabilities[0, generated_token_id].item()

        # Print the token ID and its probability
        # print(f"Token {i + 1}: ID {generated_token_id}, Probability: {generated_token_prob}")

        # sequence_likelihood *= generated_token_prob
        sequence_likelihood += math.log(generated_token_prob, 10)

    sequence_likelihood = math.pow(10, sequence_likelihood)
    # print("sequence likelihood:", sequence_likelihood)
    return sequence_likelihood

def compute_p_true(grader_input_ids, grader_outputs):
    target_word_probability = None

    # Tokenize the target word
    true_token_id = tokenizer.encode("True", add_special_tokens=False)[0]
    false_token_id = tokenizer.encode("False", add_special_tokens=False)[0]

    for i, logits in enumerate(grader_outputs['logits']):
        # Apply softmax over the last dimension (vocab size) to get probabilities
        probabilities = F.softmax(logits, dim=-1)

        # Get the index of the generated token for this step
        generated_token_id = grader_outputs['sequences'][0][grader_input_ids.shape[-1] + i].item()

        # Check if this token matches the target word
        if generated_token_id == true_token_id:
            target_word_probability = probabilities[0, generated_token_id].item()  # Extract probability for the target word
            print(f"P(True) = {target_word_probability}")
            return target_word_probability
        if generated_token_id == false_token_id:
            target_word_probability = probabilities[0, generated_token_id].item()
            print(f"P(False) = {target_word_probability}")
            return 1 - target_word_probability
    print("target word not found")
    return 0.5

In [ ]:
def read_jsonl(file_path):
  flat_data = []
  with open(file_path, 'r') as f:
      for line in f:
          record = json.loads(line)
          flat_data.append(record)
  return flat_data

def save_to_csv(data, filename):
    # Check if file exists and if it's empty to write headers only once
    try:
        with open(filename, 'a', newline='') as file:
            writer = csv.DictWriter(file, fieldnames=data[0].keys())
            writer.writeheader()
            writer.writerows(data)
    except FileExistsError:
        with open(filename, 'w', newline='') as file:
            writer = csv.DictWriter(file, fieldnames=data[0].keys())
            writer.writerows(data)

### Regex

In [ ]:
def extract_answer(text):
    # Regular expression pattern to match everything after "[Answer]: "
    # pattern = r"\[Answer\]:\s*(.*)"
    pattern = r"\[Answer\]:\s*(.*?)(?:\n|$)"
    match = re.search(pattern, text, re.DOTALL)
    if match:
        answer_text = match.group(1)
        return answer_text
    else:
        print("No match found")
        return ""

def extract_reasoning(text):
    # Regular expression pattern to match everything after "[Reasoning]: "
    pattern = r"\[Reasoning\]:\s*(.*?)(?:\n|$)"
    match = re.search(pattern, text, re.DOTALL)
    if match:
        reasoning = match.group(1)
        return reasoning
    else:
        print("No match found")
        return ""

def extract_reflection(text):
    # Regular expression pattern to match everything after "[Reflection]: "
    pattern = r"\[Reflection\]:\s*(.*?)(?:\n|$)"
    match = re.search(pattern, text, re.DOTALL)
    if match:
        reflection = match.group(1)
        return reflection
    else:
        print("No match found")
        return ""

### Semantic Clustering

In [ ]:
import torch
import numpy as np
from transformers import AutoModelForSequenceClassification, AutoTokenizer
from sklearn.cluster import AgglomerativeClustering

# Load the DeBERTa-based NLI model (for entailment)
# Assumes the model outputs probabilities for "entailment", "neutral", "contradiction" (in that order)
nli_model_name = "MoritzLaurer/mDeBERTa-v3-base-mnli-xnli"
nli_tokenizer = AutoTokenizer.from_pretrained(nli_model_name)
nli_model = AutoModelForSequenceClassification.from_pretrained(nli_model_name)
nli_model.eval()

def compute_entailment_score(premise, hypothesis):
    """
    Compute the entailment probability (score for the "entailment" label) between two sentences
    using a DeBERTa-based NLI model.

    Here, we assume that the model outputs probabilities in the order:
    [entailment, neutral, contradiction].
    """
    inputs = nli_tokenizer.encode_plus(premise, hypothesis, return_tensors="pt", truncation=True)
    with torch.no_grad():
        logits = nli_model(**inputs).logits
    # For this model, we assume the 0-th index corresponds to "entailment".
    entail_prob = torch.softmax(logits, dim=-1)[0, 0].item()
    return entail_prob

def semantic_clustering(answers, entail_threshold=0.8):
    """
    Given a list of generated answers, compute semantic clusters using the NLI model.
    Two answers are considered semantically equivalent (and placed in the same cluster)
    if the maximum entailment score (in either direction) exceeds entail_threshold.

    Returns:
        cluster_labels: a list of integer cluster labels (one for each answer).
    """
    n = len(answers)
    # Build an n x n similarity matrix using entailment scores.
    sim = np.zeros((n, n))
    for i in range(n):
        for j in range(i, n):
            if i == j:
                sim[i, j] = 1.0
            else:
                score1 = compute_entailment_score(answers[i], answers[j])
                score2 = compute_entailment_score(answers[j], answers[i])
                score = max(score1, score2)
                sim[i, j] = sim[j, i] = score
    # Convert similarity to a distance matrix.
    distance = 1 - sim
    # Use Agglomerative Clustering with a distance threshold.
    clustering = AgglomerativeClustering(
        n_clusters=None,
        linkage='average',
        distance_threshold=1 - entail_threshold
    )
    cluster_labels = clustering.fit_predict(distance)
    return cluster_labels

tokenizer_config.json:   0%|          | 0.00/1.26k [00:00<?, ?B/s]

spm.model:   0%|          | 0.00/4.31M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/16.3M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/286 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.07k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/558M [00:00<?, ?B/s]

### Predictive Entropy (PE) and Semantic Entropy (SE)

In [ ]:
def predictive_entropy(log_probs):
    """
    Computes the MC estimate of the predictive entropy:
      E[-log p(x)] ~= -1/N sum_i log p(x_i)
    """
    return -np.sum(log_probs) / len(log_probs)

def predictive_entropy_rao(log_probs):
    """
    Computes an alternative entropy estimate:
      - sum(exp(log_probs)*log_probs)
    """
    return -np.sum(np.exp(log_probs) * log_probs)

def logsumexp_by_id(semantic_ids, log_likelihoods, agg='sum_normalized'):
    """
    Group log likelihoods by their semantic cluster (given by semantic_ids)
    and compute a log-sum-exp aggregation.
    """
    unique_ids = sorted(list(set(semantic_ids)))
    log_likelihood_per_semantic_id = []
    for uid in unique_ids:
        indices = [i for i, x in enumerate(semantic_ids) if x == uid]
        id_log_liks = [log_likelihoods[i] for i in indices]
        if agg == 'sum_normalized':
            # Normalize by the total probability mass over all generations.
            norm = np.log(np.sum(np.exp(log_likelihoods)))
            log_lik_norm = np.array(id_log_liks) - norm
            logsumexp_value = np.log(np.sum(np.exp(log_lik_norm)))
        else:
            raise ValueError("Unknown aggregation method")
        log_likelihood_per_semantic_id.append(logsumexp_value)
    return log_likelihood_per_semantic_id

In [ ]:
def get_avg_log_likelihoods(input_ids, outputs, num_generations):
    responses = []
    avg_log_likelihoods = []
    log_likelihoods = []

    # The generated sequences (shape: [num_generations, sequence_length])
    sequences = outputs.sequences.cpu().numpy().tolist()
    scores = outputs.logits  # list of tensors (length = generated tokens)
    input_length = input_ids.shape[1]

    # For each generation, compute the average log probability over generated tokens.
    for i in range(num_generations):
        gen_ids = sequences[i]
        # Only consider the generated tokens (exclude the prompt tokens).
        gen_token_ids = gen_ids[input_length:]
        token_log_probs = []
        for t, token_id in enumerate(gen_token_ids):
            # Each time-step's score tensor has shape (num_generations, vocab_size)
            score_t = scores[t][i]  # get scores for the t-th token of generation i
            log_probs_t = F.log_softmax(score_t, dim=-1)
            token_log_prob = log_probs_t[token_id].item()
            token_log_probs.append(token_log_prob)
        print("token_log_probs:", token_log_probs)
        log_likelihoods.append(np.sum(token_log_probs))
        avg_lp = np.mean(token_log_probs) if token_log_probs else float('-inf')
        print("avg_lp:", avg_lp)
        avg_log_likelihoods.append(avg_lp)
        generated_text = tokenizer.decode(gen_ids, skip_special_tokens=True)
        responses.append(generated_text)

    print("avg_log_likelihoods:", avg_log_likelihoods)
    return responses, avg_log_likelihoods, log_likelihoods


def compute_uncertainties(input_ids, outputs, num_generations):
    responses, avg_log_likelihoods, log_likelihoods = get_avg_log_likelihoods(input_ids, outputs, num_generations)

    # Compute predictive entropy (token-level uncertainty).
    pred_entropy = predictive_entropy(avg_log_likelihoods)
    pred_entropy_real = predictive_entropy(log_likelihoods)
    print("Predictive Entropy:", pred_entropy)
    print("Predictive Entropy (unnormalised):", pred_entropy_real)

    # Compute semantic entropy:
    # 1. Group responses into clusters
    cluster_ids = semantic_clustering(responses, entail_threshold=0.8)
    # 2. Aggregate log likelihoods for each cluster.
    agg_log_likelihoods = logsumexp_by_id(cluster_ids, avg_log_likelihoods, agg='sum_normalized')
    # 3. Compute semantic entropy using the aggregated log likelihoods.
    sem_entropy = predictive_entropy_rao(agg_log_likelihoods)
    print("Semantic Entropy:", sem_entropy)

    # Optionally, print out each response with its average log likelihood and semantic id.
    for i, (resp, lp) in enumerate(zip(responses, avg_log_likelihoods)):
        print(f"\nResponse {i+1} (Semantic Cluster {cluster_ids[i]}):\n{resp}\nAvg Log Likelihood: {lp:.4f}")

    return pred_entropy, pred_entropy_real, sem_entropy

## SQuAD 2.0

In [ ]:
system_prompt = """
Let's take it step by step. You are student sitting in an reading comprehension exam. Given a question,
give the answer in a short span of text, and state your explanation in [Reasoning] section. Some of the questions may be unanswerable, in that case,
give an answer by [Answer]: Unanswerable



[Question]: When were the Normans in Normandy

Answer in the following format:

[Reasoning]: [Provide your explanation here if any]
[Answer]: [Answer here]

======
You will receive feedback from teacher in subsequent conversation, based on the feedback,
reflect on your previous answer and answer again in the following format:

[Reflection]: [Provide your reflection]
[Answer]: [Answer here]
"""

question_format = """
[Question]: {question}
[Reasoning]: [Your reasoning here]
[Answer]: [Your short answer here]
"""



grader_prompt = """
You are a grader grading a reading comprehension exam. Students are provided question,
and they give an answer together with their reasoning to derive the answer. Some of the questions may be unanswerable,
in that case, the expected [Answer] section is empty.

Answer either True or False given the student's answer.

Example 1:
[Question]: 1 + 2 * 3
[Reasoning]: Multiplication is performed before addition
[Answer]: 7

True

Example 2:
[Question]: In what country is Normandy located?
[Reasoning]: Random guess
[Answer]: China

False
"""

input_to_grader = """
[Question]: {question}
[Reasoning]: {reasoning}
[Answer]: {answer}

Is the proposed answer: True / False
"""




verbal_system_prompt = """
Let's take it step by step. You are student sitting in an reading comprehension exam. Given a question,
give the answer in a short span of text, and state your explanation in [Reasoning] section, give your confidence in a integer from 0 - 100. Some of the questions may be unanswerable, in that case,
give an answer by [Answer]: Unanswerable



[Question]: When were the Normans in Normandy

Answer in the following format:

[Reasoning]: [Provide your explanation here if any]
[Answer]: [Answer here]
[Confidence]: [Your confidence]

======
You will receive feedback from teacher in subsequent conversation, based on the feedback,
reflect on your previous answer and answer again in the following format:

[Reflection]: [Provide your reflection]
[Answer]: [Answer here]
[Confidence]: [Your confidence, between 0 - 100]
"""

verbal_question_format = """
[Question]: {question}
[Reasoning]: [Your reasoning here]
[Answer]: [Your short answer here]
[Confidence]: [Your confidence]
"""

In [ ]:
def squad_elicit_logit_confidence(question, reasoning, answer):
    grader_messages = [
        {"role": "system", "content": grader_prompt}
    ]
    formatted_question = input_to_grader.format(question=question, reasoning=reasoning, answer=answer)
    outputs, input_ids, output_messages = generate(model, tokenizer, grader_messages, formatted_question)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
    output_messages.append({"role": "assistant", "content": generated_text})
    return generated_text, outputs, input_ids, output_messages

def verbal_predict(question):
    messages = [
        {"role": "system", "content": verbal_system_prompt}
    ]
    formatted_question = verbal_question_format.format(question=question)
    outputs, input_ids, output_messages = generate(model, tokenizer, messages, formatted_question)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
    output_messages.append({"role": "assistant", "content": generated_text})
    return generated_text, outputs, input_ids, output_messages

def extract_verbal_confidence(text):
    # Regular expression pattern to match everything after "[Confidence]: "
    pattern = r"\[Confidence\]:\s*(.*?)(?:\n|$)"
    match = re.search(pattern, text, re.DOTALL)
    if match:
        confidence_text = match.group(1)
        return confidence_text
    else:
        print("No match found")
        return ""

In [ ]:
def squad_analyze_question_uncertainty(model, tokenizer, system_prompt, prompt, squad_question):
    """
    Generate multiple answers for the input question using a LLaMA model and compute various
    uncertainty metrics for the generated answers.
    Returns a dictionary with answers and their uncertainty metrics.
    """
    num_samples = 5
    # Input
    messages = [
        {"role": "system", "content": system_prompt}
    ]
    messages.append({"role": "user", "content": prompt})
    input_ids = tokenizer.apply_chat_template(
        messages,
        add_generation_prompt=True,
        return_tensors="pt"
    )
    input_ids = input_ids.to(model.device)

    terminators = [
        tokenizer.eos_token_id,
        tokenizer.convert_tokens_to_ids("<|eot_id|>")
    ]


    start_time = time.time()
    print("--- generate begins ---")

    # Generate 5 sample answers with sampling
    # We use do_sample=True for stochastic generation; adjust temperature/top_p for diversity if needed
    outputs = model.generate(
        input_ids,
        max_new_tokens=512, # limit length of the answer
        num_return_sequences=num_samples, # number of answers to sample
        eos_token_id=terminators,
        do_sample=True,
        temperature=0.6, # sampling temperature
        top_p=0.9, # use top-p sampling for diversity
        output_scores=True,
        output_logits=True,
        output_attentions=True,
        return_dict_in_generate=True
    )
    # print(outputs)

    print("--- generate ends, time taken: %s seconds ---" % (time.time() - start_time))

    # Decode generated sequences and isolate the answer text (exclude the question prompt)
    generated_sequences = outputs.sequences  # tensor of shape (5, prompt_len + answer_len)
    prompt_len = input_ids.shape[-1]
    answers = []
    for seq in generated_sequences:
        answer_tokens = seq[prompt_len:]  # tokens after the prompt
        # Remove any EOS token from the end of the answer
        answer_tokens = answer_tokens.tolist()
        if tokenizer.eos_token_id in answer_tokens:
            eos_index = answer_tokens.index(tokenizer.eos_token_id)
            answer_tokens = answer_tokens[:eos_index]
        answer_text = tokenizer.decode(answer_tokens, skip_special_tokens=True).strip()
        answers.append(answer_text)

    # 1. Sequence Likelihood
    sequence_likelihood = compute_sequence_likelihood(input_ids, outputs)

    # 2. Predictive Entropy, 5. Semantic Entropy
    predictive_entropy, predictive_entropy_real, semantic_entropy = compute_uncertainties(input_ids, outputs, num_samples)

    ########## SQuAD 2.0 only #############
    # 3. P(True) (different across dataset)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
    squad_reasoning = extract_reasoning(generated_text)
    squad_answer = extract_answer(generated_text)

    grader_text, grader_outputs, grader_input_ids, grader_messages = squad_elicit_logit_confidence(squad_question, squad_reasoning, squad_answer)
    p_true = compute_p_true(grader_input_ids, grader_outputs)
    #######################################

    def lexical_and_eccentricity(answers):
        # 4. Lexical similarity: use BLEU score to measure similarity among answers
        smoothing = SmoothingFunction().method1  # to handle short sequences zero matches
        bleu_scores = []
        for i, hyp in enumerate(answers):
            # Use all other answers as references for the i-th answer
            refs = [ans.split() for j, ans in enumerate(answers) if j != i]
            hyp_tokens = hyp.split()
            # Compute BLEU score for this hypothesis vs all other references
            if len(hyp_tokens) == 0:
                bleu = 0.0
            else:
                bleu = sentence_bleu(refs, hyp_tokens, smoothing_function=smoothing)
            bleu_scores.append(bleu)
        # 4. Lexical similarity metric: average self-BLEU score (how similar each answer is to others)
        lexical_similarity = sum(bleu_scores) / len(bleu_scores) if bleu_scores else 0.0

        # 6. Eccentricity: use sentence embeddings to measure semantic dispersion
        embedder = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")
        embeddings = embedder.encode(answers, convert_to_numpy=True)

        # Compute eccentricity: max distance of any embedding from the mean embedding
        if num_samples > 0:
            mean_embedding = np.mean(embeddings, axis=0)
            # Euclidean distances from mean
            distances = [float(np.linalg.norm(embed - mean_embedding)) for embed in embeddings]
            eccentricity = max(distances)
        else:
            eccentricity = 0.0

        return lexical_similarity, eccentricity

    lexical_similarity, eccentricity = lexical_and_eccentricity(answers)

    ########## SQuAD 2.0 only #############
    lexical_similarity_answer_only, eccentricity_answer_only = lexical_and_eccentricity(list(map(extract_answer, answers)))

    # 7. Verbalised Confidence
    prediction_full_ver, _, _, _ = verbal_predict(squad_question)
    verbalised_confidence = extract_verbal_confidence(prediction_full_ver)
    verbal_predicted_answer = extract_answer(prediction_full_ver)

    #######################################

    # Prepare output data structure
    results = {
        "question": squad_question,
        "predicted_answer": squad_answer,
        "reasoning": squad_reasoning,
        "predictions": answers,
        "sequence_likelihoods": sequence_likelihood,       # log-likelihood for each answer
        "p_true": p_true,                    # model-estimated P(True) for each answer
        "predictive_entropy": predictive_entropy,
        "predictive_entropy_real": predictive_entropy_real,
        "lexical_similarity": lexical_similarity,
        "semantic_entropy": semantic_entropy,
        "eccentricity": eccentricity,
        "lexical_similarity_answer_only": lexical_similarity_answer_only,
        "eccentricity_answer_only": eccentricity_answer_only,

        "verbal_predicted_answer": verbal_predicted_answer,
        "verbal_prediction": prediction_full_ver,
        "verbalised_confidence": verbalised_confidence
    }
    return results

In [ ]:
def squad_generate_each_question(id, question, is_impossible, answers, plausible_answers=[]):
  """
  Given:
  id, question, is_impossible, ground_truth, plausible_answers,

  Collected:
  predicted_answer, reasoning, predictions,
  1. sequence_likelihoods,
  2. predictive_entropy,
  3. p_true,
  4. lexical_similarity,
  5. semantic_entropy,
  6. eccentricity
  7. verbalised confidence & verbal_predicted_answer

  """
  result = {"id": id, "question": question, "is_impossible": is_impossible, "ground_truth": answers}
  if (len(plausible_answers) > 0):
      result["plausible_answers"] = plausible_answers
  else:
      result["plausible_answers"] = []


  prompt = question_format.format(question=question)
  temp = squad_analyze_question_uncertainty(model, tokenizer, system_prompt, prompt, question)


  result["predicted_answer"] = temp["predicted_answer"]
  result["reasoning"] = temp["reasoning"]
  result["predictions"] = temp["predictions"]
  result["sequence_likelihoods"] = temp["sequence_likelihoods"]
  result["p_true"] = temp["p_true"]
  result["predictive_entropy"] = temp["predictive_entropy"]
  result["predictive_entropy_real"] = temp["predictive_entropy_real"]
  result["lexical_similarity"] = temp["lexical_similarity"]
  result["semantic_entropy"] = temp["semantic_entropy"]
  result["eccentricity"] = temp["eccentricity"]
  result["lexical_similarity_answer_only"] = temp["lexical_similarity_answer_only"]
  result["eccentricity_answer_only"] = temp["eccentricity_answer_only"]

  result["verbal_predicted_answer"] = temp["verbal_predicted_answer"]
  result["verbalised_confidence"] = temp["verbalised_confidence"]

  print(result)
  return result

In [ ]:
question = """In what country is Normandy located?"""
prompt = question_format.format(question=question)

############## Begin ##################
# Input
messages = [
    {"role": "system", "content": system_prompt}
]
messages.append({"role": "user", "content": prompt})
input_ids = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt=True,
    return_tensors="pt"
)
input_ids = input_ids.to(model.device)

terminators = [
    tokenizer.eos_token_id,
    tokenizer.convert_tokens_to_ids("<|eot_id|>")
]

num_generations = 5

# Generate num_generations sample answers with sampling
# We use do_sample=True for stochastic generation; adjust temperature/top_p for diversity if needed
outputs = model.generate(
    input_ids,
    max_new_tokens=512, # limit length of the answer
    num_return_sequences=num_generations, # number of answers to sample
    eos_token_id=terminators,
    do_sample=True,
    temperature=0.6, # sampling temperature
    top_p=0.9, # use top-p sampling for diversity
    output_scores=True,
    output_logits=True,
    output_attentions=True,
    return_dict_in_generate=True
)

# Output: Decode generated sequences and isolate the answer text (exclude the question prompt)
generated_sequences = outputs.sequences  # tensor of shape (5, prompt_len + answer_len)
prompt_len = input_ids.shape[-1]
answers = []
for seq in generated_sequences:
    answer_tokens = seq[prompt_len:]  # tokens after the prompt
    # Remove any EOS token from the end of the answer
    answer_tokens = answer_tokens.tolist()
    if tokenizer.eos_token_id in answer_tokens:
        eos_index = answer_tokens.index(tokenizer.eos_token_id)
        answer_tokens = answer_tokens[:eos_index]
    answer_text = tokenizer.decode(answer_tokens, skip_special_tokens=True).strip()
    answers.append(answer_text)

compute_uncertainties(input_ids, outputs, num_generations)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
`torch.nn.functional.scaled_dot_product_attention` does not support `output_attentions=True`. Falling back to eager attention. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.


token_log_probs: [-8.237022848334163e-05, -0.02339346893131733, 0.0, -0.00028939827461726964, -0.45044243335723877, -0.004846017807722092, -0.03156006708741188, -0.4354369044303894, -0.14816272258758545, -0.34299784898757935, -0.977577269077301, -0.08533328026533127, -0.8247436285018921, -1.1557834148406982, -0.04863592982292175, -0.3302949070930481, -0.6937763094902039, -0.2773708403110504, -1.1874619722366333, -1.4272372722625732, -0.2563733756542206, -0.9413653612136841, -0.0031054625287652016, -0.11268933117389679, -1.2273619174957275, -0.000573351513594389, -0.09726472944021225, -0.10459090024232864, -0.4286362826824188, -0.19987955689430237, -0.5329337120056152, -0.16196182370185852, -0.20745845139026642, -0.17970262467861176, -0.8313218355178833, -0.0931691899895668, -2.1842281818389893, -1.230705976486206, -0.4332278072834015, -1.642103672027588, -0.2660735547542572, -0.3711342513561249, -4.4225667807040736e-05, -0.8078469038009644, -0.5421051383018494, -0.5641000270843506, -0.

/usr/local/lib/python3.11/dist-packages/sklearn/cluster/_agglomerative.py:588: ClusterWarning: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  out = hierarchy.linkage(X, method=linkage, metric=affinity)


(np.float64(2.412479004971037),
 np.float64(195.410799402654),
 np.float64(0.9529052506523957))

#### Archive

In [ ]:
# import numpy as np
# import torch
# from transformers import AutoTokenizer, AutoModelForSequenceClassification
# # from nltk.translate.rouge_score import rouge_scorer
# from rouge_score import rouge_scorer
# from sklearn.cluster import AgglomerativeClustering


# # Load the DeBERTa-based NLI model (for entailment)
# # Assumes the model outputs probabilities for "entailment", "neutral", "contradiction" (in that order)
# nli_model_name = "MoritzLaurer/mDeBERTa-v3-base-mnli-xnli"
# nli_tokenizer = AutoTokenizer.from_pretrained(nli_model_name)
# nli_model = AutoModelForSequenceClassification.from_pretrained(nli_model_name)
# nli_model.eval()

# def compute_entailment_score(premise, hypothesis):
#     """
#     Compute the entailment probability (score for the "entailment" label) between two sentences
#     using a DeBERTa-based NLI model.
#     """
#     inputs = nli_tokenizer.encode_plus(premise, hypothesis, return_tensors="pt", truncation=True)
#     with torch.no_grad():
#         logits = nli_model(**inputs).logits
#     # Assuming label 2 corresponds to "entailment"
#     entail_prob = torch.softmax(logits, dim=-1)[0, 0].item()
#     return entail_prob

# def semantic_clustering(answers, entail_threshold=0.8):
#     """
#     Given a list of generated answers, compute semantic clusters using an NLI model.
#     Two answers are in the same cluster if the entailment score (in either direction) exceeds entail_threshold.
#     Returns a list of cluster labels.
#     """
#     n = len(answers)
#     # Build an n x n similarity matrix using the NLI entailment scores:
#     # We consider answers i and j semantically equivalent if:
#     # max(entail(i->j), entail(j->i)) >= entail_threshold.
#     sim = np.zeros((n, n))
#     for i in range(n):
#         for j in range(i, n):
#             if i == j:
#                 sim[i, j] = 1.0
#             else:
#                 score1 = compute_entailment_score(answers[i], answers[j])
#                 score2 = compute_entailment_score(answers[j], answers[i])
#                 score = max(score1, score2)
#                 sim[i, j] = sim[j, i] = score
#     # Convert similarity to a distance matrix:
#     distance = 1 - sim
#     # Perform clustering; here using Agglomerative Clustering with a distance threshold:
#     clustering = AgglomerativeClustering(
#         n_clusters=None,
#         # affinity='precomputed',
#         linkage='average',
#         distance_threshold=1 - entail_threshold
#     )
#     cluster_labels = clustering.fit_predict(distance)
#     return cluster_labels

# def compute_lexical_similarity(answers):
#     """
#     Compute average pairwise lexical similarity among answers using ROUGE-L F1 score.
#     """
#     scorer = rouge_scorer.RougeScorer(['rougeL'], use_stemmer=True)
#     n = len(answers)
#     scores = []
#     affinity_matrix = np.zeros((n, n))
#     for i in range(n):
#         for j in range(n):
#             if i == j:
#                 affinity_matrix[i, j] = 1.0
#             elif i < j:
#                 score = scorer.score(answers[i], answers[j])['rougeL'].fmeasure
#                 affinity_matrix[i, j] = affinity_matrix[j, i] = score
#                 scores.append(score)
#     avg_score = np.mean(scores) if scores else 1.0
#     return avg_score, affinity_matrix

# def compute_spectral_eccentricity(affinity_matrix):
#     """
#     Given a symmetric affinity matrix (from lexical similarity), compute a spectral
#     measure of dispersion (eccentricity) from the normalized Laplacian.
#     """
#     # Degree matrix
#     D = np.diag(affinity_matrix.sum(axis=1))
#     # Compute symmetric normalized Laplacian: L = I - D^(-1/2) * W * D^(-1/2)
#     with np.errstate(divide='ignore'):
#         D_inv_sqrt = np.diag(1.0 / np.sqrt(np.diag(D)))
#     D_inv_sqrt[np.isinf(D_inv_sqrt)] = 0.0
#     I = np.eye(affinity_matrix.shape[0])
#     L = I - D_inv_sqrt @ affinity_matrix @ D_inv_sqrt
#     # Compute eigenvalues of L
#     eigvals = np.linalg.eigvalsh(L)
#     # As a simple eccentricity measure, we use the L2 norm of (1 - eigenvalues)
#     eccentricity = np.linalg.norm(1 - eigvals)
#     return eccentricity

# def compute_uncertainty_measures(input_ids, outputs, answers, entail_threshold=0.8):
#     """
#     Given a list of generated answers from a Llama model on SQuAD 2.0,
#     compute:
#       1. Semantic uncertainty: normalized number of clusters using DeBERTa NLI-based entailment.
#       2. Lexical similarity: average pairwise ROUGE-L F1 score.
#       3. Spectral eccentricity: computed from the ROUGE-L-based affinity matrix.
#     Returns a dict with the computed measures.
#     """
#     print("[compute_uncertainty_measure] answer:", answers)
#     # Semantic clustering using NLI entailment scores
#     cluster_labels = semantic_clustering(answers, entail_threshold=entail_threshold)

#     print("[compute_uncertainty_measure] cluster_labels:", cluster_labels)

#     # Semantic entropy
#     semantic_entropy = compute_semantic_entropy(input_ids, outputs, cluster_labels)

#     # Lexical similarity and affinity matrix
#     avg_lex_sim, affinity_matrix = compute_lexical_similarity(answers)

#     # Spectral eccentricity from the affinity (lexical similarity) graph
#     spectral_ecc = compute_spectral_eccentricity(affinity_matrix)

#     return {
#         'semantic_entropy': semantic_entropy,  # normalized number of semantic clusters (higher => more uncertainty)
#         'lexical_similarity': avg_lex_sim,          # higher implies lower uncertainty
#         'eccentricity': spectral_ecc           # higher implies higher dispersion/uncertainty
#     }


# context = """The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries."""
# question = """In what country is Normandy located?"""
# prompt = question_format.format(context=context, question=question)

# messages = [
#     {"role": "system", "content": system_prompt}
# ]
# messages.append({"role": "user", "content": prompt})
# input_ids = tokenizer.apply_chat_template(
#     messages,
#     add_generation_prompt=True,
#     return_tensors="pt"
# )
# input_ids = input_ids.to(model.device)

# terminators = [
#     tokenizer.eos_token_id,
#     tokenizer.convert_tokens_to_ids("<|eot_id|>")
# ]


# start_time = time.time()
# print("--- generate begins ---")

# # Generate 5 sample answers with sampling
# # We use do_sample=True for stochastic generation; adjust temperature/top_p for diversity if needed
# outputs = model.generate(
#     input_ids,
#     max_new_tokens=512, # limit length of the answer
#     num_return_sequences=5, # number of answers to sample
#     eos_token_id=terminators,
#     do_sample=True,
#     temperature=0.6, # sampling temperature
#     top_p=0.9, # use top-p sampling for diversity
#     output_scores=True,
#     output_logits=True,
#     output_attentions=True,
#     return_dict_in_generate=True
# )
# # print(outputs)

# print("--- generate ends, time taken: %s seconds ---" % (time.time() - start_time))

# # Decode generated sequences and isolate the answer text (exclude the question prompt)
# generated_sequences = outputs.sequences  # tensor of shape (5, prompt_len + answer_len)
# prompt_len = input_ids.shape[-1]
# answers = []
# for seq in generated_sequences:
#     answer_tokens = seq[prompt_len:]  # tokens after the prompt
#     # Remove any EOS token from the end of the answer
#     answer_tokens = answer_tokens.tolist()
#     if tokenizer.eos_token_id in answer_tokens:
#         eos_index = answer_tokens.index(tokenizer.eos_token_id)
#         answer_tokens = answer_tokens[:eos_index]
#     answer_text = tokenizer.decode(answer_tokens, skip_special_tokens=True).strip()
#     answers.append(answer_text)

# measures = compute_uncertainty_measures(input_ids, outputs, answers, entail_threshold=0.8)
# print("Uncertainty Measures:")
# for key, val in measures.items():
#     print(f"{key}: {val:.4f}")

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


--- generate begins ---
--- generate ends, time taken: 19.36697244644165 seconds ---
[compute_uncertainty_measure] answer: ['[Answer]: France\n\n[Reasoning]: According to the context, Normandy is mentioned as a "region in France". The name "Normandy" itself is derived from the Normans, who were a people who gave their name to the region. This establishes a clear geographical connection between the Normans and the region of Normandy.', '[Answer]: Normandy is located in France.\n\n[Reasoning]: The context explicitly states that Normandy is a "region in France", providing clear information about its location.', '[Answer]: France\n\n[Reasoning]: The context mentions that the Normans gave their name to Normandy, a region in France, and it also states that Normandy is a region in France. This information directly answers the question about the location of Normandy.', '[Answer]: France\n\n[Reasoning]: The context directly mentions "a region in France" as the location of Normandy, indicating t

/usr/local/lib/python3.11/dist-packages/sklearn/cluster/_agglomerative.py:588: ClusterWarning: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  out = hierarchy.linkage(X, method=linkage, metric=affinity)


In [ ]:
# def squad_analyze_question_uncertainty(model, tokenizer, system_prompt, prompt, squad_context, squad_question):
#     """
#     Generate multiple answers for the input question using a LLaMA model and compute various
#     uncertainty metrics for the generated answers.
#     Returns a dictionary with answers and their uncertainty metrics.
#     """
#     num_samples = 5
#     # Input
#     messages = [
#         {"role": "system", "content": system_prompt}
#     ]
#     messages.append({"role": "user", "content": prompt})
#     input_ids = tokenizer.apply_chat_template(
#         messages,
#         add_generation_prompt=True,
#         return_tensors="pt"
#     )
#     input_ids = input_ids.to(model.device)

#     terminators = [
#         tokenizer.eos_token_id,
#         tokenizer.convert_tokens_to_ids("<|eot_id|>")
#     ]


#     start_time = time.time()
#     print("--- generate begins ---")

#     # Generate 5 sample answers with sampling
#     # We use do_sample=True for stochastic generation; adjust temperature/top_p for diversity if needed
#     outputs = model.generate(
#         input_ids,
#         max_new_tokens=512, # limit length of the answer
#         num_return_sequences=num_samples, # number of answers to sample
#         eos_token_id=terminators,
#         do_sample=True,
#         temperature=0.6, # sampling temperature
#         top_p=0.9, # use top-p sampling for diversity
#         output_scores=True,
#         output_logits=True,
#         output_attentions=True,
#         return_dict_in_generate=True
#     )
#     print(outputs)

#     print("--- generate ends, time taken: %s seconds ---" % (time.time() - start_time))

#     # Decode generated sequences and isolate the answer text (exclude the question prompt)
#     generated_sequences = outputs.sequences  # tensor of shape (5, prompt_len + answer_len)
#     prompt_len = input_ids.shape[-1]
#     answers = []
#     for seq in generated_sequences:
#         answer_tokens = seq[prompt_len:]  # tokens after the prompt
#         # Remove any EOS token from the end of the answer
#         answer_tokens = answer_tokens.tolist()
#         if tokenizer.eos_token_id in answer_tokens:
#             eos_index = answer_tokens.index(tokenizer.eos_token_id)
#             answer_tokens = answer_tokens[:eos_index]
#         answer_text = tokenizer.decode(answer_tokens, skip_special_tokens=True).strip()
#         answers.append(answer_text)

#     # 1. Sequence Likelihood, 2. Predictive Entropy
#     sequence_likelihood = compute_sequence_likelihood(input_ids, outputs)
#     predictive_entropy = sum(compute_predictive_entropy(outputs.scores)) / num_samples



#     ########## SQuAD 2.0 only #############
#     # 3. P(True) (different across dataset)
#     generated_ids = outputs['sequences']
#     generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
#     squad_reasoning = extract_reasoning(generated_text)
#     squad_answer = extract_answer(generated_text)

#     grader_text, grader_outputs, grader_input_ids, grader_messages = squad_elicit_logit_confidence(squad_context, squad_question, squad_reasoning, squad_answer)
#     p_true = compute_p_true(grader_input_ids, grader_outputs)
#     #######################################

#     # 4. Lexical similarity: use BLEU score to measure similarity among answers
#     smoothing = SmoothingFunction().method1  # to handle short sequences zero matches
#     bleu_scores = []
#     for i, hyp in enumerate(answers):
#         # Use all other answers as references for the i-th answer
#         refs = [ans.split() for j, ans in enumerate(answers) if j != i]
#         hyp_tokens = hyp.split()
#         # Compute BLEU score for this hypothesis vs all other references
#         if len(hyp_tokens) == 0:
#             bleu = 0.0
#         else:
#             bleu = sentence_bleu(refs, hyp_tokens, smoothing_function=smoothing)
#         bleu_scores.append(bleu)
#     # 4. Lexical similarity metric: average self-BLEU score (how similar each answer is to others)
#     lexical_similarity = sum(bleu_scores) / len(bleu_scores) if bleu_scores else 0.0

#     # 5. Semantic Entropy and 6. Eccentricity: use sentence embeddings to measure semantic dispersion
#     embedder = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")
#     embeddings = embedder.encode(answers, convert_to_numpy=True)
#     # Compute cosine similarity matrix for clustering
#     n = len(embeddings)
#     cos_sim_matrix = [[0.0]*n for _ in range(n)]
#     for i in range(n):
#         for j in range(n):
#             if i == j:
#                 cos_sim_matrix[i][j] = 1.0
#             else:
#                 # cosine similarity = (a·b) / (||a||*||b||)
#                 dot = float(np.dot(embeddings[i], embeddings[j]))
#                 norm_i = float(np.linalg.norm(embeddings[i]))
#                 norm_j = float(np.linalg.norm(embeddings[j]))
#                 cos_sim_matrix[i][j] = dot / (norm_i * norm_j + 1e-12)
#     # Cluster answers: treat answers with cosine sim above 0.85 as same semantic cluster
#     threshold = 0.85
#     parent = list(range(n))
#     def find(x):
#         if parent[x] != x:
#             parent[x] = find(parent[x])
#         return parent[x]
#     def union(x, y):
#         rx, ry = find(x), find(y)
#         if rx != ry:
#             parent[ry] = rx
#     for i in range(n):
#         for j in range(i+1, n):
#             if cos_sim_matrix[i][j] >= threshold:
#                 union(i, j)
#     # Determine clusters
#     clusters = {}
#     for i in range(n):
#         root = find(i)
#         clusters.setdefault(root, []).append(i)
#     cluster_sizes = [len(idx_list) for idx_list in clusters.values()]
#     # Compute entropy of cluster size distribution
#     semantic_entropy = 0.0
#     for size in cluster_sizes:
#         p = size / float(n)
#         if p > 0:
#             semantic_entropy -= p * math.log(p)
#     # Compute eccentricity: max distance of any embedding from the mean embedding
#     if n > 0:
#         mean_embedding = np.mean(embeddings, axis=0)
#         # Euclidean distances from mean
#         distances = [float(np.linalg.norm(embed - mean_embedding)) for embed in embeddings]
#         eccentricity = max(distances)
#     else:
#         eccentricity = 0.0

#     # Prepare output data structure
#     results = {
#         "question": question,
#         "answers": answers,
#         "sequence_likelihoods": sequence_likelihood,       # log-likelihood for each answer
#         "p_true": p_true,                    # model-estimated P(True) for each answer
#         "predictive_entropy": predictive_entropy,
#         "lexical_similarity": lexical_similarity,
#         "semantic_entropy": semantic_entropy,
#         "eccentricity": eccentricity,
#         "lexical_similarity_answer_only": lexical_similarity_answer_only,
#         "semantic_entropy_answer_only": semantic_entropy_answer_only,
#         "eccentricity_answer_only": eccentricity_answer_only
#     }
#     return results

In [ ]:
# def squad_analyze_question_uncertainty(model, tokenizer, system_prompt, prompt, squad_context, squad_question):
#     """
#     Generate multiple answers for the input question using a LLaMA model and compute various
#     uncertainty metrics for the generated answers.
#     Returns a dictionary with answers and their uncertainty metrics.
#     """
#     num_samples = 10
#     # Input
#     messages = [
#         {"role": "system", "content": system_prompt}
#     ]
#     messages.append({"role": "user", "content": prompt})
#     input_ids = tokenizer.apply_chat_template(
#         messages,
#         add_generation_prompt=True,
#         return_tensors="pt"
#     )
#     input_ids = input_ids.to(model.device)

#     terminators = [
#         tokenizer.eos_token_id,
#         tokenizer.convert_tokens_to_ids("<|eot_id|>")
#     ]


#     start_time = time.time()
#     print("--- generate begins ---")

#     # Generate 5 sample answers with sampling
#     # We use do_sample=True for stochastic generation; adjust temperature/top_p for diversity if needed
#     outputs = model.generate(
#         input_ids,
#         max_new_tokens=512, # limit length of the answer
#         num_return_sequences=num_samples, # number of answers to sample
#         eos_token_id=terminators,
#         do_sample=True,
#         temperature=0.6, # sampling temperature
#         top_p=0.9, # use top-p sampling for diversity
#         output_scores=True,
#         output_logits=True,
#         output_attentions=True,
#         return_dict_in_generate=True
#     )
#     # print(outputs)

#     print("--- generate ends, time taken: %s seconds ---" % (time.time() - start_time))

#     # Decode generated sequences and isolate the answer text (exclude the question prompt)
#     generated_sequences = outputs.sequences  # tensor of shape (5, prompt_len + answer_len)
#     prompt_len = input_ids.shape[-1]
#     answers = []
#     for seq in generated_sequences:
#         answer_tokens = seq[prompt_len:]  # tokens after the prompt
#         # Remove any EOS token from the end of the answer
#         answer_tokens = answer_tokens.tolist()
#         if tokenizer.eos_token_id in answer_tokens:
#             eos_index = answer_tokens.index(tokenizer.eos_token_id)
#             answer_tokens = answer_tokens[:eos_index]
#         answer_text = tokenizer.decode(answer_tokens, skip_special_tokens=True).strip()
#         answers.append(answer_text)

#     # 1. Sequence Likelihood
#     sequence_likelihood = compute_sequence_likelihood(input_ids, outputs)
#     predictive_entropy = sum(compute_predictive_entropy(outputs.scores)) / num_samples

#     # 2. Predictive Entropy
#     def get_predictive_entropy():
#         # log likelihoods (one tensor per sample)
#         log_likelihoods_samples = []

#         model.eval()
#         with torch.no_grad():
#             for _ in range(num_samples):
#                 # Forward pass to get logits; shape: [batch_size, seq_length, vocab_size]
#                 outputs = model(input_ids=input_ids)
#                 logits = outputs.logits

#                 # Compute log probabilities over the vocabulary
#                 log_probs = F.log_softmax(logits, dim=-1)

#                 # Gather the log probability for each token in the input
#                 # input_ids shape: [batch_size, seq_length]
#                 token_log_probs = log_probs.gather(dim=-1, index=input_ids.unsqueeze(-1)).squeeze(-1)  # [1, seq_length]

#                 # Remove batch dimension and store sample; shape: [seq_length]
#                 log_likelihoods_samples.append(token_log_probs.squeeze(0))

#         # Stack samples to obtain a tensor of shape [num_samples, seq_length]
#         log_likelihoods = torch.stack(log_likelihoods_samples)  # shape: [num_samples, seq_length]

#         # Compute the log-average probability for each token in a numerically stable way:
#         # log_avg[i] = logsumexp(log_likelihoods[:, i]) - log(num_samples)
#         n = log_likelihoods.shape[0]
#         log_avg = torch.logsumexp(log_likelihoods, dim=0) - torch.log(torch.tensor(n, dtype=log_likelihoods.dtype, device=log_likelihoods.device))

#         # Convert log-average probabilities to probabilities
#         avg_probs = torch.exp(log_avg)

#         # Compute per-token entropy: -p * log(p)
#         token_entropy = -avg_probs * log_avg

#         # Average the token entropy over the sequence length to get a scalar value
#         predictive_entropy = token_entropy.mean()

#         return predictive_entropy.item()

#     predictive_entropy = get_predictive_entropy()


#     ########## SQuAD 2.0 only #############
#     # 3. P(True) (different across dataset)
#     generated_ids = outputs['sequences']
#     generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
#     squad_reasoning = extract_reasoning(generated_text)
#     squad_answer = extract_answer(generated_text)

#     grader_text, grader_outputs, grader_input_ids, grader_messages = squad_elicit_logit_confidence(squad_context, squad_question, squad_reasoning, squad_answer)
#     p_true = compute_p_true(grader_input_ids, grader_outputs)
#     #######################################

#     def compute_entropy(answers):
#         # 4. Lexical similarity: use BLEU score to measure similarity among answers
#         smoothing = SmoothingFunction().method1  # to handle short sequences zero matches
#         bleu_scores = []
#         for i, hyp in enumerate(answers):
#             # Use all other answers as references for the i-th answer
#             refs = [ans.split() for j, ans in enumerate(answers) if j != i]
#             hyp_tokens = hyp.split()
#             # Compute BLEU score for this hypothesis vs all other references
#             if len(hyp_tokens) == 0:
#                 bleu = 0.0
#             else:
#                 bleu = sentence_bleu(refs, hyp_tokens, smoothing_function=smoothing)
#             bleu_scores.append(bleu)
#         # 4. Lexical similarity metric: average self-BLEU score (how similar each answer is to others)
#         lexical_similarity = sum(bleu_scores) / len(bleu_scores) if bleu_scores else 0.0

#         # 5. Semantic Entropy and 6. Eccentricity: use sentence embeddings to measure semantic dispersion
#         embedder = SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")
#         embeddings = embedder.encode(answers, convert_to_numpy=True)
#         # Compute cosine similarity matrix for clustering
#         n = len(embeddings)
#         cos_sim_matrix = [[0.0]*n for _ in range(n)]
#         for i in range(n):
#             for j in range(n):
#                 if i == j:
#                     cos_sim_matrix[i][j] = 1.0
#                 else:
#                     # cosine similarity = (a·b) / (||a||*||b||)
#                     dot = float(np.dot(embeddings[i], embeddings[j]))
#                     norm_i = float(np.linalg.norm(embeddings[i]))
#                     norm_j = float(np.linalg.norm(embeddings[j]))
#                     cos_sim_matrix[i][j] = dot / (norm_i * norm_j + 1e-12)
#         # Cluster answers: treat answers with cosine sim above 0.85 as same semantic cluster
#         threshold = 0.85
#         parent = list(range(n))
#         def find(x):
#             if parent[x] != x:
#                 parent[x] = find(parent[x])
#             return parent[x]
#         def union(x, y):
#             rx, ry = find(x), find(y)
#             if rx != ry:
#                 parent[ry] = rx
#         for i in range(n):
#             for j in range(i+1, n):
#                 if cos_sim_matrix[i][j] >= threshold:
#                     union(i, j)
#         # Determine clusters
#         clusters = {}
#         for i in range(n):
#             root = find(i)
#             clusters.setdefault(root, []).append(i)
#         cluster_sizes = [len(idx_list) for idx_list in clusters.values()]
#         # Compute entropy of cluster size distribution
#         semantic_entropy = 0
#         for size in cluster_sizes:
#             p = size / float(n)
#             if p > 0:
#                 semantic_entropy -= p * math.log(p)
#         # Compute eccentricity: max distance of any embedding from the mean embedding
#         if n > 0:
#             mean_embedding = np.mean(embeddings, axis=0)
#             # Euclidean distances from mean
#             distances = [float(np.linalg.norm(embed - mean_embedding)) for embed in embeddings]
#             eccentricity = max(distances)
#         else:
#             eccentricity = 0.0

#         return lexical_similarity, semantic_entropy, eccentricity

#     lexical_similarity, semantic_entropy, eccentricity = compute_entropy(answers)

#     ########## SQuAD 2.0 only #############
#     lexical_similarity_answer_only, semantic_entropy_answer_only, eccentricity_answer_only = compute_entropy(list(map(extract_answer, answers)))





#     # 7. Verbalised Confidence




#     prediction_full_ver, _, _, _ = verbal_predict(squad_context, squad_question)
#     verbalised_confidence = extract_verbal_confidence(prediction_full_ver)
#     verbal_predicted_answer = extract_answer(prediction_full_ver)



#     #######################################

#     # Prepare output data structure
#     results = {
#         "question": squad_question,
#         "predicted_answer": squad_answer,
#         "reasoning": squad_reasoning,
#         "predictions": answers,
#         "sequence_likelihoods": sequence_likelihood,       # log-likelihood for each answer
#         "p_true": p_true,                    # model-estimated P(True) for each answer
#         "predictive_entropy": predictive_entropy,
#         "lexical_similarity": lexical_similarity,
#         "semantic_entropy": semantic_entropy,
#         "eccentricity": eccentricity,
#         "lexical_similarity_answer_only": lexical_similarity_answer_only,
#         "semantic_entropy_answer_only": semantic_entropy_answer_only,
#         "eccentricity_answer_only": eccentricity_answer_only,

#         "verbal_predicted_answer": verbal_predicted_answer,
#         "verbal_prediction": prediction_full_ver,
#         "verbalised_confidence": verbalised_confidence
#     }
#     return results

## Data Collection

In [ ]:
drive.mount('/content/drive')

dataset_path = '/content/drive/My Drive/Experiment/squad2.jsonl'

dataset = read_jsonl(dataset_path)

def experiment1(begin, end):
    batch = 10
    experiment_results = []

    os.makedirs("output", exist_ok=True)  # Ensure output directory exists

    for count, record in enumerate(dataset[begin:end + 1], 1):
        # Replace with your actual experiment function
        # experiment_result = squad_generate_each_question(...)
        experiment_result = squad_generate_each_question(
          record['id'],
          record['question'],
          record['is_impossible'],
          record['answers'],
          record['plausible_answers']
        )

        experiment_results.append(experiment_result)
        print(f"{count}: {experiment_result}")

        if count % batch == 0 and len(experiment_results) > 0:
            filename = f"output/squad_nc_e1_{begin + count - batch}_{begin + count - 1}.csv"
            with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
                fieldnames = experiment_results[0].keys()
                writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
                writer.writeheader()
                writer.writerows(experiment_results)

            print(f"Saved chunk {begin + count - batch} to {begin + count - 1} to {filename}")
            experiment_results = []

    # Save any remaining results
    if experiment_results:
        filename = f"output/squad_nc_e1_last_{end}.csv"
        with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
            fieldnames = experiment_results[0].keys()
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            writer.writeheader()
            writer.writerows(experiment_results)

        print(f"Saved remaining chunk to {filename}")


experiment1(0, 199)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
--- generate begins ---
--- generate ends, time taken: 5.05150580406189 seconds ---
token_log_probs: [-8.237022848334163e-05, -0.02339346893131733, 0.0, -0.00028939827461726964, -0.45044243335723877, -0.004846017807722092, -0.03156006708741188, -0.4354369044303894, -0.14816272258758545, -0.34299784898757935, -0.727577269077301, -0.08263871818780899, -1.0338877439498901, -1.911265254020691, -0.4298149645328522, -0.6546767354011536, -0.7587166428565979, -0.0007814691052772105, -0.08302377164363861, -1.2057186365127563, -0.09979993104934692, -0.006723755970597267, -0.7055627107620239, -0.0012540103634819388, -0.0003301552205812186, -1.2824358940124512, -0.8390205502510071, -0.45245805382728577, -0.3602551817893982, -7.402622577501461e-05, -0.0035936555359512568, -1.5616295058862306e-05, -0.509347140789032, -0.11482524126768112, -5.483612312673358e-06, -0.0013938

/usr/local/lib/python3.11/dist-packages/sklearn/cluster/_agglomerative.py:588: ClusterWarning: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  out = hierarchy.linkage(X, method=linkage, metric=affinity)
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


Semantic Entropy: 0.41762352668326197

Response 1 (Semantic Cluster 4):
system

Cutting Knowledge Date: December 2023
Today Date: 26 Jul 2024

Let's take it step by step. You are student sitting in an reading comprehension exam. Given a question,
give the answer in a short span of text, and state your explanation in [Reasoning] section. Some of the questions may be unanswerable, in that case,
give an answer by [Answer]: Unanswerable



[Question]: When were the Normans in Normandy

Answer in the following format:

[Reasoning]: [Provide your explanation here if any]
[Answer]: [Answer here]

You will receive feedback from teacher in subsequent conversation, based on the feedback,
reflect on your previous answer and answer again in the following format:

[Reflection]: [Provide your reflection]
[Answer]: [Answer here]user

[Question]: In what country is Normandy located?
[Reasoning]: [Your reasoning here]
[Answer]: [Your short answer here]assistant

[Reasoning]: Normandy is a historical an

modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

...

--- generate ends, time taken: 3.0681405067443848 seconds ---
{'id': '5ad3fe0d604f3c001a3ffc1d', 'question': 'What was a centre of ivorywork in the 1100s?', 'is_impossible': True, 'ground_truth': [], 'plausible_answers': [{'text': 'Lombard Salerno', 'answer_start': 549}], 'predicted_answer': 'Nuremberg', 'reasoning': "I'm not aware of a specific centre of ivorywork in the 1100s, but I do know that the Middle Ages were a time of significant artistic and cultural development. I'm going to take a guess that the centre might be in a region known for its artistic or trade connections.", 'predictions': ["[Reasoning]: I'm not aware of a specific centre of ivorywork in the 1100s, but I do know that the Middle Ages were a time of significant artistic and cultural development. I'm going to take a guess that the centre might be in a region known for its artistic or trade connections.\n\n[Answer]: Nuremberg", '[Reasoning]: I am not familiar with any specific centres of ivorywork in the 1100s. Howe

/usr/local/lib/python3.11/dist-packages/sklearn/cluster/_agglomerative.py:588: ClusterWarning: The symmetric non-negative hollow observation matrix looks suspiciously like an uncondensed distance matrix
  out = hierarchy.linkage(X, method=linkage, metric=affinity)
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


Semantic Entropy: 0.9315048934766226

Response 1 (Semantic Cluster 3):
system

Cutting Knowledge Date: December 2023
Today Date: 26 Jul 2024

Let's take it step by step. You are student sitting in an reading comprehension exam. Given a question,
give the answer in a short span of text, and state your explanation in [Reasoning] section. Some of the questions may be unanswerable, in that case,
give an answer by [Answer]: Unanswerable



[Question]: When were the Normans in Normandy

Answer in the following format:

[Reasoning]: [Provide your explanation here if any]
[Answer]: [Answer here]

You will receive feedback from teacher in subsequent conversation, based on the feedback,
reflect on your previous answer and answer again in the following format:

[Reflection]: [Provide your reflection]
[Answer]: [Answer here]user

[Question]: In what century did important classical music developments occur in Normandy?
[Reasoning]: [Your reasoning here]
[Answer]: [Your short answer here]assistant



The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


--- generate begins ---
--- generate ends, time taken: 2.6779043674468994 seconds ---
{'id': '56de51c64396321400ee27f7', 'question': 'In what century did important classical music developments occur in Normandy?', 'is_impossible': False, 'ground_truth': [{'text': '11th', 'answer_start': 97}, {'text': 'the 11th', 'answer_start': 93}, {'text': '11th', 'answer_start': 97}], 'plausible_answers': [], 'predicted_answer': '17th century', 'reasoning': "There isn't enough information in the question to pinpoint the exact century. However, I can try to provide a general answer based on historical knowledge about Normandy and classical music.", 'predictions': ["[Reasoning]: There isn't enough information in the question to pinpoint the exact century. However, I can try to provide a general answer based on historical knowledge about Normandy and classical music.\n\n[Answer]: 17th century", "[Reasoning]: I'm not aware of any significant classical music developments specifically occurring in Normand

# Experiment 2

Experiment 2.1
Low confidence (Expected: Abstain to answer), Medium confidence (High Uncertainty), High confidence (Expected: consistent, won't change its answer)

Experiment 2.2
P(True)
Pre-reflection and Post-reflection and Iterative (3 reflections)

In [ ]:
system_prompt = """
Let's take it step by step. You are student sitting in an reading comprehension exam. Given a question,
give the answer in a short span of text, and state your explanation in [Reasoning] section. Some of the questions may be unanswerable, in that case,
give an answer by [Answer]: Unanswerable



[Question]: When were the Normans in Normandy

Answer in the following format:

[Reasoning]: [Provide your explanation here if any]
[Answer]: [Answer here]

======
You will receive feedback from teacher in subsequent conversation, based on the feedback,
reflect on your previous answer and answer again in the following format:

[Reflection]: [Provide your reflection]
[Answer]: [Answer here]
"""

question_format = """
[Question]: {question}
[Reasoning]: [Your reasoning here]
[Answer]: [Your short answer here]
"""

In [ ]:
reflection_prompt = """
Here is the confidence score of your previous reasoning and answer:
{confidence} / 1.0


Based on the feedback, reflect on your previous answer and answer again in the following format:

[Reflection]: [Provide your reflection]
[Answer]: [Answer here]

If you are uncertain about your answer, answer by [Answer]: Unanswerable
"""

def reflect(messages, confidence):
    formatted_reflection_prompt = reflection_prompt.format(confidence=confidence)
    outputs, input_ids, output_messages = generate(model, tokenizer, messages, formatted_reflection_prompt)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
    print("Post reflection:", generated_text)
    return generated_text, outputs, input_ids, output_messages


post_reflection_grader_prompt = """
Here is another attempt on the question after the student reflected on the feedback he received.

[Reflection]: {reflection}
[Answer]: {answer}

Is the proposed answer: True / False
Answer only True or False
"""

def elicit_logit_confidence_post_reflection(grader_messages, reflection, answer):
    formatted_question = post_reflection_grader_prompt.format(reflection=reflection, answer=answer)
    outputs, input_ids, output_messages = generate(model, tokenizer, grader_messages, formatted_question)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)
    output_messages.append({"role": "assistant", "content": generated_text})
    return generated_text, outputs, input_ids, output_messages

In [ ]:
def squad_marginalised_reflection(model, tokenizer, system_prompt, squad_question):
    # Input
    messages = [
        {"role": "system", "content": system_prompt}
    ]
    prompt = question_format.format(question=squad_question)

    # First attempt
    outputs, input_ids, messages = generate(model, tokenizer, messages, prompt)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)

    ########## SQuAD 2.0 only ############# (different across dataset)
    squad_reasoning = extract_reasoning(generated_text)
    squad_answer = extract_answer(generated_text)

    grader_text, grader_outputs, grader_input_ids, grader_messages = squad_elicit_logit_confidence(squad_question, squad_reasoning, squad_answer)
    p_true = compute_p_true(grader_input_ids, grader_outputs)
    #######################################

    messages.append({"role": "assistant", "content": generated_text})

    results = {
        "predicted_answer": squad_answer,
        "reasoning": squad_reasoning,
        "predictions": generated_text,
        "p_true": p_true
    }
    ##############################
    # Reflection (Low confidence)
    squad_full_reflection_low, _, _, _ = reflect(messages.copy(), 0.1)

    squad_reflection_low = extract_reflection(squad_full_reflection_low)
    squad_answer_low = extract_answer(squad_full_reflection_low)

    grader_text_low, grader_outputs, grader_input_ids, _ = elicit_logit_confidence_post_reflection(grader_messages.copy(), squad_reflection_low, squad_answer_low)
    p_true_post_reflection_low = compute_p_true(grader_input_ids, grader_outputs)

    # messages.append({"role": "assistant", "content": generated_text})

    results["squad_full_reflection_low"] = squad_full_reflection_low
    results["squad_answer_low"] = squad_answer_low
    results["p_true_post_reflection_low"] = p_true_post_reflection_low
    results["grader_text_low"] = grader_text_low

    ##############################
    # Reflection (Neutral confidence)
    squad_full_reflection_neutral, _, _, _ = reflect(messages.copy(), 0.5)

    squad_reflection_neutral = extract_reflection(squad_full_reflection_neutral)
    squad_answer_neutral = extract_answer(squad_full_reflection_neutral)

    grader_text_neutral, grader_outputs, grader_input_ids, _ = elicit_logit_confidence_post_reflection(grader_messages.copy(), squad_reflection_neutral, squad_answer_neutral)
    p_true_post_reflection_neutral = compute_p_true(grader_input_ids, grader_outputs)

    # messages.append({"role": "assistant", "content": generated_text})

    results["squad_full_reflection_neutral"] = squad_full_reflection_neutral
    results["squad_answer_neutral"] = squad_answer_neutral
    results["p_true_post_reflection_neutral"] = p_true_post_reflection_neutral
    results["grader_text_neutral"] = grader_text_neutral

    ##############################
    # Reflection (High confidence)
    squad_full_reflection_high, _, _, _ = reflect(messages.copy(), 0.9)

    squad_reflection_high = extract_reflection(squad_full_reflection_high)
    squad_answer_high = extract_answer(squad_full_reflection_high)

    grader_text_high, grader_outputs, grader_input_ids, _ = elicit_logit_confidence_post_reflection(grader_messages.copy(), squad_reflection_high, squad_answer_high)
    p_true_post_reflection_high = compute_p_true(grader_input_ids, grader_outputs)

    # messages.append({"role": "assistant", "content": generated_text})

    results["squad_full_reflection_high"] = squad_full_reflection_high
    results["squad_answer_high"] = squad_answer_high
    results["p_true_post_reflection_high"] = p_true_post_reflection_high
    results["grader_text_high"] = grader_text_high

    return results

In [ ]:
def squad_iterative_reflection(model, tokenizer, system_prompt, squad_question):
    # Input
    messages = [
        {"role": "system", "content": system_prompt}
    ]
    prompt = question_format.format(question=squad_question)

    # First attempt
    outputs, input_ids, messages = generate(model, tokenizer, messages, prompt)
    generated_ids = outputs['sequences']
    generated_text = tokenizer.decode(generated_ids[0][input_ids.shape[-1]:], skip_special_tokens=True)

    ########## SQuAD 2.0 only ############# (different across dataset)
    # P(True) 0
    squad_reasoning0 = extract_reasoning(generated_text)
    squad_answer0 = extract_answer(generated_text)

    grader_text, grader_outputs, grader_input_ids, grader_messages = squad_elicit_logit_confidence(squad_question, squad_reasoning0, squad_answer0)
    p_true0 = compute_p_true(grader_input_ids, grader_outputs)
    #######################################

    messages.append({"role": "assistant", "content": generated_text})

    results = {
        "predicted_answer0": squad_answer0,
        "reasoning0": squad_reasoning0,
        "predictions0": generated_text,
        "p_true0": p_true0,
        "grader_text0": grader_text
    }
    ##############################
    # First reflection
    generated_text, outputs, input_ids, messages = reflect(messages, p_true0)

    squad_reflection1 = extract_reflection(generated_text)
    squad_answer1 = extract_answer(generated_text)

    # P(True) 1
    grader_text, grader_outputs, grader_input_ids, grader_messages = elicit_logit_confidence_post_reflection(grader_messages, squad_reflection1, squad_answer1)
    p_true1 = compute_p_true(grader_input_ids, grader_outputs)

    messages.append({"role": "assistant", "content": generated_text})

    results["predicted_answer1"] = squad_answer1
    results["reflection1"] = squad_reflection1
    results["predictions1"] = generated_text
    results["p_true1"] = p_true1
    results["grader_text1"] = grader_text

    ##############################
    # Second reflection
    generated_text, outputs, input_ids, messages = reflect(messages, p_true1)

    squad_reflection2 = extract_reflection(generated_text)
    squad_answer2 = extract_answer(generated_text)
    # P(True) 2
    grader_text, grader_outputs, grader_input_ids, grader_messages = elicit_logit_confidence_post_reflection(grader_messages, squad_reflection2, squad_answer2)
    p_true2 = compute_p_true(grader_input_ids, grader_outputs)

    results["predicted_answer2"] = squad_answer2
    results["reflection2"] = squad_reflection2
    results["predictions2"] = generated_text
    results["p_true2"] = p_true2
    results["grader_text2"] = grader_text

    messages.append({"role": "assistant", "content": generated_text})

    ##############################
    # Third reflection
    generated_text, outputs, input_ids, messages = reflect(messages, p_true2)

    squad_reflection3 = extract_reflection(generated_text)
    squad_answer3 = extract_answer(generated_text)
    # P(True) 3
    grader_text, grader_outputs, grader_input_ids, grader_messages = elicit_logit_confidence_post_reflection(grader_messages, squad_reflection3, squad_answer3)
    p_true3 = compute_p_true(grader_input_ids, grader_outputs)

    results["predicted_answer3"] = squad_answer3
    results["reflection3"] = squad_reflection3
    results["predictions3"] = generated_text
    results["p_true3"] = p_true3
    results["grader_text3"] = grader_text

    messages.append({"role": "assistant", "content": generated_text})

    return results

In [ ]:
question = """In what country is Normandy located?"""

squad_question = question

squad_marginalised_reflection(model, tokenizer, system_prompt, squad_question)
squad_iterative_reflection(model, tokenizer, system_prompt, squad_question)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.
The attention mask is not set and cannot be inferred from input because pad token is same as eos token. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.


--- generate begins ---


`torch.nn.functional.scaled_dot_product_attention` does not support `output_attentions=True`. Falling back to eager attention. This warning can be removed using the argument `attn_implementation="eager"` when loading the model.
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


--- generate ends, time taken: 4.80964207649231 seconds ---
--- generate begins ---


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


...

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


--- generate ends, time taken: 2.0297069549560547 seconds ---
P(True) = 0.8805230259895325
--- generate begins ---


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


--- generate ends, time taken: 5.7382354736328125 seconds ---
Post reflection: [Reflection]: I'm glad I was able to improve my confidence score. Upon re-reading the context, I realize that I should have stuck to the information provided. The text explicitly states that the Normans "gave their name to Normandy, a region in France." This sentence strongly suggests that Normandy is indeed located in France, as it is the region where the Normans established themselves.

[Answer]: Normandy is located in France.
--- generate begins ---
--- generate ends, time taken: 2.340683698654175 seconds ---
P(False) = 0.7546109557151794
{'predicted_answer0': 'Normandy is located in France.', 'reasoning0': 'The context clearly states that Normandy is a region in France, and it mentions that the Normans gave their name to Normandy. This implies that Normandy is a part of the country where the Normans settled and established their identity.', 'predictions0': '[Answer]: Normandy is located in France.\n\n[Re

{'predicted_answer0': 'Normandy is located in France.',
 'reasoning0': 'The context clearly states that Normandy is a region in France, and it mentions that the Normans gave their name to Normandy. This implies that Normandy is a part of the country where the Normans settled and established their identity.',
 'predictions0': '[Answer]: Normandy is located in France.\n\n[Reasoning]: The context clearly states that Normandy is a region in France, and it mentions that the Normans gave their name to Normandy. This implies that Normandy is a part of the country where the Normans settled and established their identity.',
 'p_true0': 0.7263882160186768,
 'grader_text0': 'True',
 'predicted_answer1': 'Unanswerable',
 'reflection1': 'Upon re-reading the context, I realize that I made an assumption that the Normans were the original inhabitants of Normandy. However, the text explicitly states that the Normans were descended from Norse raiders and pirates who settled in the region. This implies t

## Data Collection

### Part 2.1

In [ ]:
def squad_generate_each_question_part2_1(id, question, is_impossible, answers, plausible_answers=[]):
  """
  Given:
  id, question, is_impossible, ground_truth, plausible_answers,
  """
  result = {"id": id, "question": question, "is_impossible": is_impossible, "ground_truth": answers}
  if (len(plausible_answers) > 0):
      result["plausible_answers"] = plausible_answers
  else:
      result["plausible_answers"] = []

  temp = squad_marginalised_reflection(model, tokenizer, system_prompt, question)


  result["predicted_answer"] = temp["predicted_answer"]
  result["reasoning"] = temp["reasoning"]
  result["predictions"] = temp["predictions"]
  result["p_true"] = temp["p_true"]

  result["squad_full_reflection_low"] = temp["squad_full_reflection_low"]
  result["squad_answer_low"] = temp["squad_answer_low"]
  result["p_true_post_reflection_low"] = temp["p_true_post_reflection_low"]
  result["grader_text_low"] = temp["grader_text_low"]

  result["squad_full_reflection_neutral"] = temp["squad_full_reflection_neutral"]
  result["squad_answer_neutral"] = temp["squad_answer_neutral"]
  result["p_true_post_reflection_neutral"] = temp["p_true_post_reflection_neutral"]
  result["grader_text_neutral"] = temp["grader_text_neutral"]

  result["squad_full_reflection_high"] = temp["squad_full_reflection_high"]
  result["squad_answer_high"] = temp["squad_answer_high"]
  result["p_true_post_reflection_high"] = temp["p_true_post_reflection_high"]
  result["grader_text_high"] = temp["grader_text_high"]

  print(result)
  return result

In [ ]:
drive.mount('/content/drive')

dataset_path = '/content/drive/My Drive/Experiment/squad2.jsonl'

dataset = read_jsonl(dataset_path)

def experiment2_1(begin, end):
    batch = 10
    experiment_results = []

    os.makedirs("output", exist_ok=True)  # Ensure output directory exists

    for count, record in enumerate(dataset[begin:end + 1], 1):
        # Replace with your actual experiment function
        # experiment_result = squad_generate_each_question(...)

        experiment_result = squad_generate_each_question_part2_1(
          record['id'],
          record['question'],
          record['is_impossible'],
          record['answers'],
          record['plausible_answers']
        )

        experiment_results.append(experiment_result)
        print(f"{count}: {experiment_result}")

        if count % batch == 0 and len(experiment_results) > 0:
            filename = f"output/squad_nc_e2_1_{begin + count - batch}_{begin + count - 1}.csv"
            with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
                fieldnames = experiment_results[0].keys()
                writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
                writer.writeheader()
                writer.writerows(experiment_results)

            print(f"Saved chunk {begin + count - batch} to {begin + count - 1} to {filename}")
            experiment_results = []

    # Save any remaining results
    if experiment_results:
        filename = f"output/squad_nc_e2_1_last_{end}.csv"
        with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
            fieldnames = experiment_results[0].keys()
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            writer.writeheader()
            writer.writerows(experiment_results)

        print(f"Saved remaining chunk to {filename}")


experiment2_1(0, 199)

### Part 2.2

In [ ]:
def squad_generate_each_question_part2_2(id, question, is_impossible, answers, plausible_answers=[]):
    """
    Given:
    id, question, is_impossible, ground_truth, plausible_answers,
    """
    result = {"id": id, "question": question, "is_impossible": is_impossible, "ground_truth": answers}
    if (len(plausible_answers) > 0):
        result["plausible_answers"] = plausible_answers
    else:
        result["plausible_answers"] = []

    temp = squad_iterative_reflection(model, tokenizer, system_prompt, question)


    result["predicted_answer0"] = temp["predicted_answer0"]
    result["reasoning0"] = temp["reasoning0"]
    result["predictions0"] = temp["predictions0"]
    result["p_true0"] = temp["p_true0"]
    result["grader_text0"] = temp["grader_text0"]

    result["predicted_answer1"] = temp["predicted_answer1"]
    result["reflection1"] = temp["reflection1"]
    result["predictions1"] = temp["predictions1"]
    result["p_true1"] = temp["p_true1"]
    result["grader_text1"] = temp["grader_text1"]

    result["predicted_answer2"] = temp["predicted_answer2"]
    result["reflection2"] = temp["reflection2"]
    result["predictions2"] = temp["predictions2"]
    result["p_true2"] = temp["p_true2"]
    result["grader_text2"] = temp["grader_text2"]

    result["predicted_answer3"] = temp["predicted_answer3"]
    result["reflection3"] = temp["reflection3"]
    result["predictions3"] = temp["predictions3"]
    result["p_true3"] = temp["p_true3"]
    result["grader_text3"] = temp["grader_text3"]

    print(result)
    return result

In [ ]:
dataset = read_jsonl(dataset_path)

def experiment2_2(begin, end):
    batch = 10
    experiment_results = []

    os.makedirs("output", exist_ok=True)  # Ensure output directory exists

    for count, record in enumerate(dataset[begin:end + 1], 1):
        # Replace with your actual experiment function
        # experiment_result = squad_generate_each_question(...)
        experiment_result = squad_generate_each_question_part2_2(
          record['id'],
          record['question'],
          record['is_impossible'],
          record['answers'],
          record['plausible_answers']
        )

        experiment_results.append(experiment_result)
        print(f"{count}: {experiment_result}")

        if count % batch == 0 and len(experiment_results) > 0:
            filename = f"output/squad_nc_e2_2_{begin + count - batch}_{begin + count - 1}.csv"
            with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
                fieldnames = experiment_results[0].keys()
                writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
                writer.writeheader()
                writer.writerows(experiment_results)

            print(f"Saved chunk {begin + count - batch} to {begin + count - 1} to {filename}")
            experiment_results = []

    # Save any remaining results
    if experiment_results:
        filename = f"output/squad_nc_e2_2_last_{end}.csv"
        with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
            fieldnames = experiment_results[0].keys()
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            writer.writeheader()
            writer.writerows(experiment_results)

        print(f"Saved remaining chunk to {filename}")


experiment2_2(0, 199)

# New Section

### Test

In [ ]:
context = """The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries."""
question = """In what country is Normandy located?"""

prompt = question_format.format(context=context, question=question)
squad_context = context,
squad_question = question
print("prompt:", prompt)
print("squad_context:", squad_context)
print("squad_question:", squad_question)

prompt: 
[Context]: The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.
[Question]: In what country is Normandy located?
[Reasoning]: [Your reasoning here]
[Answer]: [Your short answer here]

squad_context: ('The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th a

In [ ]:
squad_analyze_question_uncertainty(model, tokenizer, system_prompt, prompt, squad_context, squad_question)

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


Streaming output truncated to the last 5000 lines.
           5.4321e-03, 1.7776e-03]]]], device='cuda:0', dtype=torch.bfloat16), tensor([[[[5.0391e-01, 3.0708e-04, 7.6890e-06,  ..., 5.3955e-02,
           1.1914e-01, 2.5195e-01]],

         [[5.8594e-01, 1.9150e-03, 8.5354e-05,  ..., 3.1738e-02,
           8.0566e-02, 2.2461e-01]],

         [[2.8125e-01, 1.3733e-04, 8.2254e-06,  ..., 3.4904e-04,
           5.1498e-04, 9.7046e-03]],

         ...,

         [[4.4141e-01, 3.3379e-04, 1.7643e-05,  ..., 1.5015e-02,
           2.9907e-02, 4.0527e-02]],

         [[6.3672e-01, 1.1368e-03, 3.5048e-05,  ..., 3.6133e-02,
           1.8555e-02, 8.0566e-02]],

         [[4.3750e-01, 4.5204e-04, 4.0770e-05,  ..., 1.4954e-02,
           1.7700e-02, 2.2095e-02]]],


        [[[4.5312e-01, 1.0967e-04, 1.7136e-06,  ..., 2.8320e-01,
           1.4941e-01, 6.4697e-03]],

         [[5.2344e-01, 1.7548e-04, 3.2187e-06,  ..., 8.6426e-02,
           3.0273e-01, 7.2754e-02]],

         [[3.2422e-01, 2.5940

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:128009 for open-end generation.


--- generate begins ---
--- generate ends, time taken: 2.8701822757720947 seconds ---
P(True) = 0.6692123413085938 0.6692123413085938


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

...

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

{'question': 'In what country is Normandy located?',
 'answers': ['[Answer]: France\n\n[Reasoning]: According to the context, Normandy is described as a "region in France". The term "Normandy" itself is derived from the Normans, a people who originated in the region, and it is mentioned that they gave their name to Normandy, indicating that the region is indeed in France.',
  '[Answer]: France\n\n[Reasoning]: According to the given context, Normandy is a region in France, and it was given its name by the Normans, who were the people who inhabited that region.',
  '[Answer]: France\n\n[Reasoning]: According to the given context, Normandy is mentioned as a region in France. The context explicitly states that the Normans gave their name to Normandy, indicating that Normandy is a geographical location associated with the Normans.',
  '[Answer]: France\n\n[Reasoning]: According to the given context, Normandy is described as a "region in France". This information directly states the location

## GSM8K

## TruthfulQA

In [ ]:
# dataset = [i for i in range(53)]

# def experiment1(begin, end):
#     batch = 10
#     experiment_results = []

#     os.makedirs("output", exist_ok=True)  # Ensure output directory exists

#     for count, record in enumerate(dataset[begin:end + 1], 1):
#         # Replace with your actual experiment function
#         # experiment_result = squad_generate_each_question(...)
#         experiment_result = {"record": record}
#         experiment_results.append(experiment_result)
#         print(f"{count}: {experiment_result}")

#         if count % batch == 0 and len(experiment_results) > 0:
#             filename = f"output/test_e1_{begin + count - batch}_{begin + count - 1}.csv"
#             with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
#                 fieldnames = experiment_results[0].keys()
#                 writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
#                 writer.writeheader()
#                 writer.writerows(experiment_results)

#             print(f"Saved chunk {begin + count - batch} to {begin + count - 1} to {filename}")
#             experiment_results = []

#     # Save any remaining results
#     if experiment_results:
#         filename = f"output/test_e1_last_{end}.csv"
#         with open(filename, mode="w", newline="", encoding="utf-8") as csvfile:
#             fieldnames = experiment_results[0].keys()
#             writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
#             writer.writeheader()
#             writer.writerows(experiment_results)

#         print(f"Saved remaining chunk to {filename}")


# experiment1(0, 99)